In [1]:
import numpy as np
import pandas as pd
from sklearn.neighbors import NearestNeighbors

In [7]:
books = pd.read_csv("book-crossing/books.csv", sep=';', error_bad_lines=False, encoding='latin-1')
ratings = pd.read_csv("book-crossing/ratings.csv", sep=';', error_bad_lines=False, encoding='latin-1')
users = pd.read_csv("book-crossing/users.csv", sep=';', error_bad_lines=False, encoding='latin-1')
pd.set_option("display.max_rows", None, "display.max_columns", None, 'display.max_colwidth', -1)

b'Skipping line 6452: expected 8 fields, saw 9\nSkipping line 43667: expected 8 fields, saw 10\nSkipping line 51751: expected 8 fields, saw 9\n'
b'Skipping line 92038: expected 8 fields, saw 9\nSkipping line 104319: expected 8 fields, saw 9\nSkipping line 121768: expected 8 fields, saw 9\n'
b'Skipping line 144058: expected 8 fields, saw 9\nSkipping line 150789: expected 8 fields, saw 9\nSkipping line 157128: expected 8 fields, saw 9\nSkipping line 180189: expected 8 fields, saw 9\nSkipping line 185738: expected 8 fields, saw 9\n'
b'Skipping line 209388: expected 8 fields, saw 9\nSkipping line 220626: expected 8 fields, saw 9\nSkipping line 227933: expected 8 fields, saw 11\nSkipping line 228957: expected 8 fields, saw 10\nSkipping line 245933: expected 8 fields, saw 9\nSkipping line 251296: expected 8 fields, saw 9\nSkipping line 259941: expected 8 fields, saw 9\nSkipping line 261529: expected 8 fields, saw 9\n'
C:\Users\Firel\anaconda3\lib\site-packages\IPython\core\interactiveshell.p

In [8]:
books.head()

ISBN  \
0  0195153448   
1  0002005018   
2  0060973129   
3  0374157065   
4  0393045218   

                                                                                           Book-Title  \
0  Classical Mythology                                                                                  
1  Clara Callan                                                                                         
2  Decision in Normandy                                                                                 
3  Flu: The Story of the Great Influenza Pandemic of 1918 and the Search for the Virus That Caused It   
4  The Mummies of Urumchi                                                                               

            Book-Author Year-Of-Publication                   Publisher  \
0  Mark P. O. Morford    2002                Oxford University Press      
1  Richard Bruce Wright  2001                HarperFlamingo Canada        
2  Carlo D'Este          1991                HarperPerennial              
3  Gina Bari Kolata      1999                Farrar Straus Giroux         
4  E. J. W. Barber       1999                W. W. Norton &amp; Company   

                                                    Image-URL-S  \
0  http://images.amazon.com/images/P/0195153448.01.THUMBZZZ.jpg   
1  http://images.amazon.com/images/P/0002005018.01.THUMBZZZ.jpg   
2  http://images.amazon.com/images/P/0060973129.01.THUMBZZZ.jpg   
3  http://images.amazon.com/images/P/0374157065.01.THUMBZZZ.jpg   
4  http://images.amazon.com/images/P/0393045218.01.THUMBZZZ.jpg   

                                                    Image-URL-M  \
0  http://images.amazon.com/images/P/0195153448.01.MZZZZZZZ.jpg   
1  http://images.amazon.com/images/P/0002005018.01.MZZZZZZZ.jpg   
2  http://images.amazon.com/images/P/0060973129.01.MZZZZZZZ.jpg   
3  http://images.amazon.com/images/P/0374157065.01.MZZZZZZZ.jpg   
4  http://images.amazon.com/images/P/0393045218.01.MZZZZZZZ.jpg   

                                                    Image-URL-L  
0  http://images.amazon.com/images/P/0195153448.01.LZZZZZZZ.jpg  
1  http://images.amazon.com/images/P/0002005018.01.LZZZZZZZ.jpg  
2  http://images.amazon.com/images/P/0060973129.01.LZZZZZZZ.jpg  
3  http://images.amazon.com/images/P/0374157065.01.LZZZZZZZ.jpg  
4  http://images.amazon.com/images/P/0393045218.01.LZZZZZZZ.jpg

In [9]:
# Drop irrelevant features

books = books.drop(['Image-URL-S', 'Image-URL-M', 'Image-URL-L'], axis=1)
books.head()

ISBN  \
0  0195153448   
1  0002005018   
2  0060973129   
3  0374157065   
4  0393045218   

                                                                                           Book-Title  \
0  Classical Mythology                                                                                  
1  Clara Callan                                                                                         
2  Decision in Normandy                                                                                 
3  Flu: The Story of the Great Influenza Pandemic of 1918 and the Search for the Virus That Caused It   
4  The Mummies of Urumchi                                                                               

            Book-Author Year-Of-Publication                   Publisher  
0  Mark P. O. Morford    2002                Oxford University Press     
1  Richard Bruce Wright  2001                HarperFlamingo Canada       
2  Carlo D'Este          1991                HarperPerennial             
3  Gina Bari Kolata      1999                Farrar Straus Giroux        
4  E. J. W. Barber       1999                W. W. Norton &amp; Company

In [10]:
# Check for missing values

books.loc[(books['ISBN'].isnull() | books['Book-Title'].isnull() | books['Book-Author'].isnull()), :]

ISBN                                                Book-Title  \
187689  9627982032  The Credit Suisse Guide to Managing Your Personal Wealth   

       Book-Author Year-Of-Publication                       Publisher  
187689  NaN         1995                Edinburgh Financial Publishing

In [11]:
books.loc[books['ISBN'] == '9627982032', 'Book-Author'] = 'Other'

In [12]:
books['Year-Of-Publication'].unique()

array([2002, 2001, 1991, 1999, 2000, 1993, 1996, 1988, 2004, 1998, 1994,
       2003, 1997, 1983, 1979, 1995, 1982, 1985, 1992, 1986, 1978, 1980,
       1952, 1987, 1990, 1981, 1989, 1984, 0, 1968, 1961, 1958, 1974,
       1976, 1971, 1977, 1975, 1965, 1941, 1970, 1962, 1973, 1972, 1960,
       1966, 1920, 1956, 1959, 1953, 1951, 1942, 1963, 1964, 1969, 1954,
       1950, 1967, 2005, 1957, 1940, 1937, 1955, 1946, 1936, 1930, 2011,
       1925, 1948, 1943, 1947, 1945, 1923, 2020, 1939, 1926, 1938, 2030,
       1911, 1904, 1949, 1932, 1928, 1929, 1927, 1931, 1914, 2050, 1934,
       1910, 1933, 1902, 1924, 1921, 1900, 2038, 2026, 1944, 1917, 1901,
       2010, 1908, 1906, 1935, 1806, 2021, '2000', '1995', '1999', '2004',
       '2003', '1990', '1994', '1986', '1989', '2002', '1981', '1993',
       '1983', '1982', '1976', '1991', '1977', '1998', '1992', '1996',
       '0', '1997', '2001', '1974', '1968', '1987', '1984', '1988',
       '1963', '1956', '1970', '1985', '1978', '1973', '1980'

In [24]:
books.loc[(books['Year-Of-Publication'] == 'DK Publishing Inc') | (books['Year-Of-Publication'] == 'Gallimard')]

ISBN  \
209538  078946697X   
220731  2070426769   
221678  0789466953   

                                                                                                         Book-Title  \
209538  DK Readers: Creating the X-Men, How It All Began (Level 4: Proficient Readers)\";Michael Teitelbaum"          
220731  Peuple du ciel, suivi de 'Les Bergers\";Jean-Marie Gustave Le ClÃ?Â©zio"                                      
221678  DK Readers: Creating the X-Men, How Comic Books Come to Life (Level 4: Proficient Readers)\";James Buckley"   

       Book-Author Year-Of-Publication  \
209538  2000        DK Publishing Inc    
220731  2003        Gallimard            
221678  2000        DK Publishing Inc    

                                                           Publisher  
209538  http://images.amazon.com/images/P/078946697X.01.THUMBZZZ.jpg  
220731  http://images.amazon.com/images/P/2070426769.01.THUMBZZZ.jpg  
221678  http://images.amazon.com/images/P/0789466953.01.THUMBZZZ.jpg

In [25]:
books.loc[books['ISBN'] == '078946697X', 'Book-Author'] = 'Michael Teitelbaum'
books.loc[books['ISBN'] == '078946697X', 'Year-Of-Publication'] = '2000'
books.loc[books['ISBN'] == '078946697X', 'Publisher'] = 'DK Publishing Inc'

books.loc[books['ISBN'] == '2070426769', 'Book-Author'] = 'Jean-Marie Gustave'
books.loc[books['ISBN'] == '2070426769', 'Year-Of-Publication'] = '2003'
books.loc[books['ISBN'] == '2070426769', 'Publisher'] = 'Gallimard'

books.loc[books['ISBN'] == '0789466953', 'Book-Author'] = 'James Buckley'
books.loc[books['ISBN'] == '0789466953', 'Year-Of-Publication'] = '2000'
books.loc[books['ISBN'] == '0789466953', 'Publisher'] = 'DK Publishing Inc'

In [7]:
users.head()

User-ID                            Location   Age
0  1        nyc, new york, usa                 NaN  
1  2        stockton, california, usa           18.0
2  3        moscow, yukon territory, russia    NaN  
3  4        porto, v.n.gaia, portugal           17.0
4  5        farnborough, hants, united kingdom NaN

In [8]:
print(books.shape)
print(users.shape)

(271360, 3)
(278858, 3)


In [9]:
ratings.head()

User-ID        ISBN  Book-Rating
0  276725   034545104X  0          
1  276726   0155061224  5          
2  276727   0446520802  0          
3  276729   052165615X  3          
4  276729   0521795028  6

In [10]:
# Check for missing values in any of the columns

ratings.loc[ratings['User-ID'].isnull() | ratings['ISBN'].isnull() | ratings['Book-Rating'].isnull()]

Empty DataFrame
Columns: [User-ID, ISBN, Book-Rating]
Index: []

In [11]:
# Check if the ratings span 1-10

ratings['Book-Rating'].unique()

array([ 0,  5,  3,  6,  8,  7, 10,  9,  4,  1,  2], dtype=int64)

In [12]:
# Eliminate implicit feedback

ratings = ratings[ratings['Book-Rating'] != 0]

In [13]:
ratings.shape

(433671, 3)

In [14]:
# Keep only ratings that correspond to user and book datasets

ratings = ratings[ratings['ISBN'].isin(books['ISBN'])]
ratings = ratings[ratings['User-ID'].isin(users['User-ID'])]
ratings.shape

(383842, 3)

In [15]:
ratings.head()

User-ID        ISBN  Book-Rating
1   276726   0155061224  5          
3   276729   052165615X  3          
4   276729   0521795028  6          
8   276744   038550120X  7          
16  276747   0060517794  9

In [16]:
# Dataset too large for pivoting
# Reduce the dataset, filter out books with less than 5 ratings

popular_books = ratings['ISBN'].value_counts()
popular_books = popular_books[popular_books > 10]

reduced_ratings = ratings[ratings['ISBN'].isin(popular_books.index)]
reduced_ratings.shape

(132736, 3)

In [17]:
reduced_ratings.head()

User-ID        ISBN  Book-Rating
8   276744   038550120X  7          
16  276747   0060517794  9          
19  276747   0671537458  9          
20  276747   0679776818  8          
28  276754   0684867621  8

In [18]:
# Create a pivoted dataframe with user id, isbn and corresponding ratings

ratings_pivoted = reduced_ratings.pivot(index='ISBN', columns='User-ID', values='Book-Rating')
ratings_pivoted.head()

NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006547834 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550576 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550789 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0007110928 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       

User-ID     276872  276875  276887  276896  276925  276928  276929  276936  \
ISBN                                                                         
000649840X NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006547834 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550576 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550789 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0007110928 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       

User-ID     276939  276953  276957  276964  276986  276988  276994  276998  \
ISBN                                                                         
000649840X NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006547834 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550576 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550789 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0007110928 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       

User-ID     277018  277028  277036  277042  277051  277072  277087  277094  \
ISBN                                                                         
000649840X NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006547834 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550576 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550789 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0007110928 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       

User-ID     277096  277107  277109  277124  277139  277143  277157  277168  \
ISBN                                                                         
000649840X NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006547834 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550576 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550789 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0007110928 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       

User-ID     277170  277171  277179  277187  277188  277195  277197  277203  \
ISBN                                                                         
000649840X NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006547834 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550576 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550789 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0007110928 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       

User-ID     277212  277220  277228  277229  277230  277235  277237  277243  \
ISBN                                                                         
000649840X NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006547834 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550576 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550789 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0007110928 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       

User-ID     277246  277253  277257  277261  277265  277281  277284  277292  \
ISBN                                                                         
000649840X NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006547834 NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN       
0006550576 NaN     NaN     NaN    

In [19]:
# Replace NaN with 0s for the machine learning model

ratings_pivoted.fillna(value=0, inplace=True)

In [27]:
# A function that uses NearestNeighbors algorithm for finding books that are similar to the argument
# Returns the book title, author, and the cosine similarity of the book compared to the givn book

def recommended_books(model, book, n_recommendations):
    
    target_book = books.loc[books['ISBN'] == book, 'Book-Title'].values[0]
    recommended_books = []

    # n_neighbors = number of recommended books
    distances, indices = model.kneighbors(ratings_pivoted.loc[book].values.reshape(1,-1), n_neighbors = n_recommendations+1)
    cosine_similarity = 1-distances.flatten()
    
    print("Given Book:\n", target_book)
    print("Recommended Books: ")
    
    for i in range(1, len(indices.flatten())):
        isbn = ratings_pivoted.iloc[indices.flatten()[i]].name
        book_title = books.loc[books['ISBN'] == isbn, 'Book-Title'].values[0]
        book_author = books.loc[books['ISBN'] == isbn, 'Book-Author'].values[0]
        recommended_books.append([book_title, book_author, cosine_similarity[i],])
        
        print("{}) {} ({}) - {}".format(i, book_title, book_author, cosine_similarity[i]))
        
    return recommended_books

In [28]:
# Return a matrix consisting of books with the given name

def find_book(name):
    book_list = books.loc[books['Book-Title'].str.contains(name)]
    valid_books = book_list[book_list['ISBN'].isin(ratings_pivoted.index)]
    return valid_books


In [30]:
# Get matrix consisting of only Lord of the Rings
valid_books = find_book("Lord of the Rings")

# Select the first LOTR book
target_book = valid_books.iloc[1, 0]

# Set the number of recommendations
n_recommendations = 10

# Recommend books
model = NearestNeighbors(metric='cosine', algorithm='brute')
model.fit(ratings_pivoted)
predicted_books = recommended_books(model, target_book, n_recommendations)


Given Book:
 The Two Towers (The Lord of the Rings, Part 2)
Recommended Books: 
1) The Return of the King (The Lord of the Rings, Part 3) (J.R.R. TOLKIEN) - 0.5006313281926968
2) The Fellowship of the Ring (The Lord of the Rings, Part 1) (J.R.R. TOLKIEN) - 0.38012747980670136
3) The Hobbit : The Enchanting Prelude to The Lord of the Rings (J.R.R. TOLKIEN) - 0.226759064510903
4) The Silmarillion (J.R.R. TOLKIEN) - 0.1508342296725229
5) The Fellowship of the Ring (The Lord of the Rings, Part 1) (J. R. R. Tolkien) - 0.1022811796504326
6) Rainbow Valley (Anne of Green Gables Novels (Paperback)) (L. M. Montgomery) - 0.09730503715031946
7) Faith of the Fallen (Sword of Truth, Book 6) (Terry Goodkind) - 0.09252286337610283
8) Soul of the Fire (Sword of Truth, Book 5) (Terry Goodkind) - 0.0909883588910827
9) Anne of Ingleside (Anne of Green Gables Novels (Paperback)) (L.M. MONTGOMERY) - 0.09042084085334512
10) Mind-Speakers' Call (The Ghatti's Tale, Book 2) (Gayle Greeno) - 0.08157981638704093